In [1]:
from io import BytesIO

In [10]:
i = BytesIO()

In [31]:
i.write(b"fasfasffaf" * int(1e6))

10000000

In [32]:
%%timeit -n 1000
i.write(b"fasfasffaf" * 100)
i.seek(0)
i.getvalue()
i.truncate(0)

302 ns ± 61.2 ns per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [33]:
i = BytesIO()

In [34]:
%%timeit -n 1000
i = BytesIO()
i.write(b"fasfasffaf" * 100)
i.getvalue()
i = BytesIO()

270 ns ± 6.92 ns per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [1]:
from io import BytesIO

In [2]:
import subprocess
import pydub

In [522]:
from pathlib import Path
from dataclasses import dataclass
     
@dataclass(slots=True)   
class Config:
    audio_pin = 17
    wake_led_pin = 4
    tts_speed = 1.075
    chat_temperature = 0.5
    max_vision_tokens = 130
    vision_temperature = 0.2
    tts_file_format = "mp3"
    wake_signal_audio = "dearearth.mp3"
    audio_input_file = "input_query.wav"
    data_dir = Path.cwd().parent / "data"
    image_input_file ="current_view.jpg"
    audio_output_file = "audio_response.mp3"
    greenhouse_gasses = ["co2", "ch4", "n2o"]

In [43]:
Device.pin_factory = MockFactory()
at = AudioTools(Button(pin=17), LED(4))

In [44]:
at.record_and_write(duration=3)

High Performance MPEG 1.0/2.0/2.5 Audio Player for Layers 1, 2 and 3
	version 1.32.4; written and copyright by Michael Hipp and others
	free software (LGPL) without any warranty but with best wishes

Playing MPEG stream 1 of 1: dearearth.mp3 ...

MPEG 1.0 L III vbr 44100 j-s

	Title:   
	Artist:  
	Album:   
	Year:    
	Genre:   
	Comment: 



[0:01] Decoding of dearearth.mp3 finished.


'input_query.wav'

In [22]:
audio_bytes.getvalue()

b'RIFF$\x08\x04\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00D\xac\x00\x00\x88X\x01\x00\x02\x00\x10\x00data\x00\x08\x04\x00\x00\x00\x00\x00\x00\x00\x01\x00\x05\x00\x10\x00\x11\x00\xe8\xff\x92\xffR\xffT\xff\x85\xff\xbf\xff\xe8\xff\xeb\xff\xe6\xff\xfe\xff\x02\x00\xed\xff\xe3\xff\xd8\xff\xf5\xff-\x00$\x00\xd7\xffu\xff2\xff\x1d\xff&\xff_\xff\xb0\xff\xe3\xff\xfa\xff\x0f\x003\x00K\x005\x00\xe1\xff\x8b\xff\x8b\xff\xde\xff\x18\x00\xe3\xffn\xff$\xff1\xff\x92\xff\xe5\xff\xf8\xff\x11\x00/\x00\'\x00\xff\xff\xef\xff\xfc\xff\xfc\xff\x05\x00\xe7\xff\xaa\xff\xaa\xff\xbe\xff\xb6\xff\xc4\xff\xe6\xff\xff\xff\x13\x00\x19\x00\x17\x00\x12\x00 \x00H\x00\x82\x00\xa0\x00V\x00\xcb\xffx\xff\x93\xff\xeb\xff\x1c\x00\x17\x00\n\x00\x07\x00\x14\x00 \x00)\x00N\x00l\x00c\x005\x00\xe0\xff\x98\xff\xac\xff\n\x00>\x00*\x00\x19\x00\x1c\x00\x0b\x00\xf1\xff\xe3\xff\x07\x00F\x00^\x00R\x00\r\x00\xd1\xff\xce\xff\xf1\xff\x1b\x00\'\x00!\x00/\x00L\x00W\x00J\x00\x1e\x00\x11\x002\x00K\x00j\x00l\x00;\x00\xfc\xff\xeb\xff\x0b\x00\x19\x00\

In [11]:
from pydub import AudioSegment

a = AudioSegment.from_file(file=at.audio_bytes, format="wav")

In [12]:
a

In [8]:
from pydub import playback

playback.play(a)

In [1]:
import pyaudio

In [2]:
p = pyaudio.PyAudio()

In [3]:
p.get_default_input_device_info()

{'index': 0,
 'structVersion': 2,
 'name': 'MacBook Pro Microphone',
 'hostApi': 0,
 'maxInputChannels': 1,
 'maxOutputChannels': 0,
 'defaultLowInputLatency': 0.05324263038548753,
 'defaultLowOutputLatency': 0.01,
 'defaultHighInputLatency': 0.06340136054421769,
 'defaultHighOutputLatency': 0.1,
 'defaultSampleRate': 44100.0}

In [11]:
import io

i = io.BytesIO()

i.write(b"hey")

3

In [12]:
print(i.getvalue())
i.close()

b'hey'


In [23]:
import pydub

In [56]:
%%timeit -n 1
from pydub.playback import play
import io
from pydub import AudioSegment

with open("dearearth.mp3", "rb") as f:
    i = io.BytesIO(f.read())
    
audio = AudioSegment.from_file(i, format="mp3")
play(audio)

2.06 s ± 16.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [ ]:
from openai import OpenAI
from copy import deepcopy

client = OpenAI()


response = client.audio.speech.create(
    model="tts-1",
    voice="echo",
    input="We love live"
)

In [ ]:
res = deepcopy(response)

In [1]:
import wave, subprocess
import pyaudio
from gpiozero import Button, LED
from multiprocessing import Queue
from gpiozero.pins.mock import MockFactory
from gpiozero import Device
# from pydub import AudioSegment
# from pydub.playback import play


class AudioTools:
    __slots__ = (
        "channels",
        "sample_rate",
        "chunk",
        "format",
        "output_file",
        "button",
        "wake_signal",
        "queue"
    )

    def __init__(self, button: Button, led: LED, queue: Queue):
        params = self.p.get_default_input_device_info()
        self.channels = int(params["maxInputChannels"])
        self.sample_rate = int(params["defaultSampleRate"])
        self.chunk = 128  # TODO: FIGURE OUT A GOOD NUMBER
        self.format = pyaudio.paInt16
        # button.when_pressed = self.record_and_write
        config = Config()
        self.output_file = config.audio_input_file
        self.wake_signal = config.wake_signal_audio
        self.queue = queue
        # self.led = led

    @property
    def p(self):
        return pyaudio.PyAudio()

    def write_audio(
        self, audio_bytes: bytes, channels: int, sample_rate: int, sample_width: int
    ) -> str:
        """Writes audio to an output file"""
        output_file = self.output_file
        with wave.open(output_file, "wb") as wf:
            wf.setnchannels(channels)
            wf.setframerate(sample_rate)
            wf.setsampwidth(sample_width)
            wf.writeframes(audio_bytes)
        return output_file

    def record_and_write(self, duration) -> str:
        """Records from microphone while the button is held down,
        returns a resulting output audio file"""
        # self.led.on()
        self.audio_playback(self.wake_signal)

        channels, sample_rate = (
            self.channels,
            self.sample_rate,
        )
        format, p, chunk = self.format, self.p, self.chunk
        stream = p.open(
            format=self.format,
            channels=self.channels,
            rate=sample_rate,
            frames_per_buffer=self.chunk,
            input=True,
        )

        audio_bytes, count = bytearray(), 0
        while  count < duration:
            for _ in range(0, int(sample_rate / chunk)):
                audio_bytes.extend(stream.read(chunk))
                self.queue.put(audio_bytes)
            count += 1
        stream.stop_stream()
        stream.close()
        p.terminate()
        output_file = self.write_audio(
            audio_bytes=bytes(audio_bytes),
            channels=channels,
            sample_rate=sample_rate,
            sample_width=p.get_sample_size(format),
        )
        # self.led.off()
        return output_file

    def audio_playback(self, audio_file):
        subprocess.Popen(["mpg123", audio_file]).wait()

In [99]:
Device.pin_factory = MockFactory()
at = AudioTools(button=Button(17), led=LED(4))

at.record_and_write(duration=4)

High Performance MPEG 1.0/2.0/2.5 Audio Player for Layers 1, 2 and 3
	version 1.32.4; written and copyright by Michael Hipp and others
	free software (LGPL) without any warranty but with best wishes

Playing MPEG stream 1 of 1: dearearth.mp3 ...

MPEG 1.0 L III vbr 44100 j-s

	Title:   
	Artist:  
	Album:   
	Year:    
	Genre:   
	Comment: 



[0:01] Decoding of dearearth.mp3 finished.


'input_query.wav'

In [100]:
at.audio_bytes

bytearray(b'\x11\x00\x12\x00\x13\x00\x14\x00\x14\x00\x14\x00\x14\x00\x16\x00\x17\x00\x17\x00\x17\x00\x17\x00\x16\x00\x15\x00\x14\x00\x14\x00\x13\x00\x12\x00\x12\x00\x12\x00\x12\x00\x11\x00\x0f\x00\x0f\x00\r\x00\x0c\x00\x0b\x00\n\x00\x0b\x00\t\x00\t\x00\x08\x00\t\x00\x08\x00\x08\x00\x08\x00\t\x00\x08\x00\n\x00\n\x00\n\x00\n\x00\x0b\x00\x0b\x00\x0c\x00\x0b\x00\x0b\x00\n\x00\n\x00\n\x00\t\x00\x08\x00\x08\x00\x07\x00\x07\x00\x06\x00\x05\x00\x04\x00\x03\x00\x02\x00\x03\x00\x02\x00\x01\x00\x00\x00\xff\xff\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xfe\xff\xfe\xff\xfc\xff\xfb\xff\xf9\xff\xfa\xff\xfa\xff\xfa\xff\xf9\xff\xf8\xff\xf8\xff\xf8\xff\xf9\xff\xf8\xff\xf8\xff\xfa\xff\xfa\xff\xf9\xff\xf8\xff\xf8\xff\xf8\xff\xf5\xff\xf4\xff\xf4\xff\xf3\xff\xf2\xff\xf0\xff\xf0\xff\xef\xff\xef\xff\xef\xff\xef\xff\xf0\xff\xf0\xff\xf0\xff\xf1\xff\xf0\xff\xf1\xff\xf1\xff\xf1\xff\xf2\xff\xf2\xff\xf1\xff\xf1\xff\xef\xff\xef\xff\xee\xff\xee\xff\xee\xff\xed\xff\xed\xff\xec\xff\xed\xff\xed\xff\xed\xff\xec\xff\xee\xff

In [91]:
import io
i = io.BytesIO()

In [92]:
with open("input_query.wav", "rb") as f:
    i.write(f.read())

In [93]:
i.getvalue()

b'RIFF$`\x05\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00D\xac\x00\x00\x88X\x01\x00\x02\x00\x10\x00data\x00`\x05\x00\x01\x00\xfe\xff\xfd\xff\xfe\xff\x00\x00\x02\x00\x01\x00\x03\x00\x04\x00\x03\x00\x04\x00\x05\x00\x05\x00\x04\x00\x05\x00\x07\x00\x07\x00\x06\x00\x07\x00\t\x00\x0b\x00\r\x00\n\x00\x08\x00\x06\x00\x08\x00\t\x00\x07\x00\x05\x00\x05\x00\n\x00\r\x00\x11\x00\x0f\x00\x0f\x00\x0f\x00\r\x00\t\x00\x07\x00\x03\x00\x02\x00\x08\x00\x0b\x00\n\x00\n\x00\x0c\x00\x0e\x00\x0f\x00\x11\x00\x12\x00\x13\x00\x15\x00\x16\x00\x14\x00\x13\x00\x13\x00\x13\x00\x13\x00\x15\x00\x16\x00\x17\x00\x16\x00\x16\x00\x16\x00\x14\x00\x14\x00\x13\x00\x14\x00\x14\x00\x13\x00\x12\x00\x12\x00\x12\x00\x13\x00\x12\x00\x13\x00\x13\x00\x15\x00\x16\x00\x17\x00\x18\x00\x19\x00\x19\x00\x19\x00\x18\x00\x19\x00\x1a\x00\x1a\x00\x18\x00\x16\x00\x16\x00\x13\x00\x13\x00\x13\x00\x15\x00\x17\x00\x18\x00\x19\x00\x19\x00\x1b\x00\x19\x00\x17\x00\x16\x00\x15\x00\x16\x00\x18\x00\x19\x00\x1a\x00\x1a\x00\x1a\x00\x1b\x00\x1b\x00\x1a\x00\

In [95]:
with wave.open("testing123.wav", "wb") as wf:
    wf.setframerate(44100)
    wf.setnchannels(1)
    wf.setsampwidth(2)
    wf.writeframes(i.getvalue())


In [103]:
a = np.frombuffer(at.audio_bytes, np.int16).flatten().astype(np.float32) / 32768.0

In [96]:
import numpy as np 

mel = whisper.log_mel_spectrogram(whisper.pad_or_trim(np.frombuffer(i.getvalue(), np.int16).flatten().astype(np.float32) / 32768.0)).to(model.device)

In [106]:
whisper.decode(model=model, mel=whisper.log_mel_spectrogram(whisper.pad_or_trim(a)), options=whisper.DecodingOptions(fp16=False))

DecodingResult(audio_features=tensor([[ 0.0550,  0.0588,  0.0448,  ...,  0.0813,  0.1790,  0.0915],
        [-0.7157, -0.6342, -0.3516,  ...,  1.0530, -0.1464,  0.4442],
        [-0.3213,  0.1888, -0.7103,  ...,  0.5179, -0.3813,  0.0991],
        ...,
        [ 0.7345, -1.7335,  0.3217,  ..., -0.1079, -0.5657,  0.3722],
        [-0.1380, -0.5260,  0.0815,  ...,  0.7076,  0.0482,  0.1998],
        [ 0.2569, -0.1157, -1.3940,  ...,  0.2665, -0.4441, -0.1101]]), language='en', language_probs=None, tokens=[50364, 8239, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174, 2174

In [1]:
cmd = [
"ffmpeg",
"-nostdin",
"-i", "-",
# "threads", "0",
"-f", "s16le",
"-ac", "1",
"-acodec", "pcm_s16le",
"-ar", str(16000),
"-", 
    
]

In [2]:
c = subprocess.run(cmd, check=True, input=at.audio_bytes, capture_output=True)

NameError: name 'subprocess' is not defined

In [167]:
mel = whisper.log_mel_spectrogram(whisper.pad_or_trim(
    np.frombuffer(c.stdout, np.int16).flatten().astype(np.float32) / 32768.0
))

In [168]:
whisper.decode(model=model, mel=mel, options=whisper.DecodingOptions(fp16=False))

DecodingResult(audio_features=tensor([[ 0.0958,  0.0683,  0.0229,  ..., -0.0722,  0.0941,  0.0123],
        [-0.7879, -0.5329,  0.2121,  ..., -0.1611,  0.2317, -0.4365],
        [ 0.2221,  1.9745,  0.2713,  ..., -0.6959, -0.6845, -0.3360],
        ...,
        [ 0.7716, -1.7335,  0.3097,  ..., -0.1118, -0.4994,  0.4368],
        [-0.1521, -0.4778,  0.0979,  ...,  0.6289,  0.0475,  0.2600],
        [ 0.2035, -0.1376, -1.4065,  ...,  0.1931, -0.4433, -0.1565]]), language='en', language_probs=None, tokens=[50364, 1449, 1520, 294, 957, 1702, 11, 4997, 484, 512, 1507, 13, 50514], text='Just check in real quick, testing out some stuff.', avg_logprob=-0.5358406816210065, no_speech_prob=0.004424481652677059, temperature=0.0, compression_ratio=0.875)

In [19]:
import subprocess
import numpy as np
cmd = [
"ffmpeg",
"-nostdin",
"-i", "-",
"-f", "s16le",
"-ac", "1",
"-acodec", "pcm_s16le",
"-ar", str(16000),
"-", 
    
]

def format_audio(audio: bytes):
    audio = subprocess.run(
        cmd, check=True, input=audio, capture_output=True
    ).stdout
    return (np.frombuffer(audio, np.int16)
            .flatten().astype(np.float32) 
            / 32768.0)


In [20]:
from multiprocessing import Process, Queue, Manager
from utils import AudioTools


manager = Manager()
value = manager.list()
# Device.pin_factory = MockFactory()

at = AudioTools(button=None, led=None, list=value)

p = Process(target=at.record_and_write, kwargs={"duration": 5})

In [21]:
import whisper
model = whisper.load_model("base")
def get_transcription(audio):
    audio = format_audio(audio)
    mel = whisper.log_mel_spectrogram(
        whisper.pad_or_trim(audio)
    )
    return whisper.decode(
        model=model, mel=mel, options=whisper.DecodingOptions(fp16=False)
    )

In [22]:
import time, wave
p.start()
count = 0
text = ""
while True:
    if value[:]:
        count += 1
        print("count")
        audio_bytes = value.pop(0)
        text += get_transcription(audio=audio_bytes).text
        # with wave.open(f"testing{count}.wav", "wb") as wf:
        #     wf.setnchannels(1)
        #     wf.setframerate(44100)
        #     wf.setsampwidth(2)
        #     wf.writeframes(audio_bytes)
        

High Performance MPEG 1.0/2.0/2.5 Audio Player for Layers 1, 2 and 3
	version 1.32.4; written and copyright by Michael Hipp and others
	free software (LGPL) without any warranty but with best wishes

Playing MPEG stream 1 of 1: dearearth.mp3 ...

MPEG 1.0 L III vbr 44100 j-s

	Title:   
	Artist:  
	Album:   
	Year:    
	Genre:   
	Comment: 



[0:01] Decoding of dearearth.mp3 finished.


1 5
2 5
count
3 5
count
4 5
count
5 5
count
count


KeyboardInterrupt: 

In [23]:
text

'making a sentence.right now. Transcribed.subscribing a sentence.Yes, we are.Thank you.'

In [5]:
import wave
with wave.open("testing123.wav", "wb") as wf:
    wf.setnchannels(1)
    wf.setframerate(44100)
    wf.setsampwidth(2)
    wf.writeframes(bytes(value[0]))

In [12]:
[][0]

IndexError: list index out of range

In [ ]:
from pydub import AudioSegment

In [ ]:
AudioSegment.from_raw(value[0], format="wav", sample_width=2)v

IndexError: list index out of range

In [25]:
import io
io.BytesIO().open()

AttributeError: '_io.BytesIO' object has no attribute 'open'

In [1]:
with open("dearearth.mp3", "rb") as f:
    print(f)

<_io.BufferedReader name='dearearth.mp3'>


In [10]:
import io

i = io.BytesIO()

# i.name = "*.mp3"

In [9]:
io.BufferedReader(i)

<_io.BufferedReader name='*.mp3'>

In [15]:
from pydub import AudioSegment
from pydub.playback import play

with open("output.mp3", "rb") as f:
    i = io.BytesIO(f.read())
    
a = AudioSegment.from_file(i, format="mp3")

play(a)

In [16]:
import subprocess
i.getvalue()

b'\xff\xf3\xe4\xc4\x00a\xfc9\xd8\x00\xe6\x9f\x881p\x14\xd0\xad\xb3p\xa9L\xd2K\x10\xa4\x8e-67\xd2\xa0\xcf\x86\xe3)\x08\x08A\x80 a\x85\x86F6\x0e\x17`\xc1\x00\xe2\x80\x08$\x02`p)\x82\x80\x08\xa0\x8a\x8ec[\x83\xe3\x18\xca\xe1\xcc%\x0e\xc4S9\x85l/\x01m\xd7\xfa\xc2;)\x0e\x98\xe9\x8e\x90\xe5\xcb/CckJ\xb0\xc1"0q\x1c\xc5G#V5\x8d\xe0\xd679\xe4\x94\xd4i\xe5\x11\xa4\x90\x86~:\x19`\\\x14\x02\x8b\x03\xcbP`PI\x87\xc5\xe6\x19\x05\x190\xc4e!QU\xa9\xe9\xfe|\xe9\x9a\xd0f\rY\xc3\xa2r\xd7\x980\x86\x81a\xb2xr\xab\x1d\x8a\x07*\x01\xd5~k\xd3\x9ar\xe3\x0c\x0e\xe6\xe3\xd1(\xc7!;<Ol\xf3\xa0\xd0\xd5\x1e\x0c\x12d\xd0\x99\xf2e\x00\x80\x02\x8cP$\xaci@\x00\xc2A\x02\xe0\xc1\xc1\xdfg\xf5\xc7}\xd6\xa4\xae!\x06\xbcKQ\xc3\x95:I\x8b\x99\xa6N\xcd1\',}\xfc\xdb?\t\xc1\x04.\n\xc41\xc3\x1a\x86\x9f4\xdc\xe0\x92\xb2^\x86\x13\x85\x01\xc8h\x16\xc2\x10t<W\xbf~\xaf~\x9fQ\xc0\x82t2<x\xc0\xc8\xde\xcf\x858\xdf\x135\x19\xce\xee\n\xbe\xca\xf7\xc7"\xa1\xb0\xb6*0\xac9\xcb\x9b9\xfe\\\xd4j\xf8\xcfV\x0b\xfa=\x80\xe4\'\x06\x82\x81\x91\xce\x06[\

In [17]:
subprocess.run(["ffplay", "-", "-nodisp", "-autoexit"], input=i.getvalue())

ffplay version 6.1.1 Copyright (c) 2003-2023 the FFmpeg developers
  built with Apple clang version 15.0.0 (clang-1500.1.0.2.5)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/6.1.1_2 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libopen

CompletedProcess(args=['ffplay', '-', '-nodisp', '-autoexit'], returncode=0)

In [175]:
import pandas as pd


product_example = {
    "name": "paperplastic",
    "materials": ["paper", "plastic"],
    "weight": [0.3, 4]
}

c = pd.json_normalize(product_example)

In [179]:
for m, w in zip(c["materials"].explode(), c["weight"].explode()):
    print(f"search for efactor {m} multiply weight of {w}")


search for efactor paper multiply weight of 0.3
search for efactor plastic multiply weight of 4


In [180]:
from pydub import AudioSegment

a = AudioSegment.from_file("audio_output.mp3")

In [181]:
from pydub.silence import detect_silence

detect_silence(a)

[[0, 10176]]

In [187]:
a.dBFS

-26.330361300550177

In [193]:
import audioop


with open("input_query.wav", "rb") as b:
    print(audioop.rms(b.read(), 2))

14047


In [197]:
import struct

import numpy as np 
import io
with open("input_query.wav", "rb") as b:
    i = io.BytesIO(b.read())

In [198]:
i.seek(0)

0

In [218]:
import scipy

scipy.io.wavfile.read(i)

(44100, array([], dtype=int16))

In [494]:
import pyaudio
import wave 
import pydub
from numbers import Number

class AudioTools:
    __slots__ = (
        "channels",
        "sample_rate",
        "chunk",
        "format",
        "output_file",
        "button",
        "wake_signal",
        "dBFS_silence_threshold"
    )

    def __init__(self):
        params = self.p.get_default_input_device_info()
        self.channels = int(params["maxInputChannels"])
        self.sample_rate = int(params["defaultSampleRate"])
        self.chunk = 128  # TODO: FIGURE OUT A GOOD NUMBER
        self.format = pyaudio.paInt16
        # button.when_pressed = self.record_and_write
        config = Config()
        self.dBFS_silence_threshold = -50
        self.output_file = config.audio_input_file
        self.wake_signal = config.wake_signal_audio
        # self.led = led

    @property
    def p(self):
        return pyaudio.PyAudio()
    
    def get_rms(self, buffer: bytes):
        audio = np.frombuffer(buffer, dtype=np.int16).astype(np.float32)
        rms = np.sqrt(np.mean(np.square(audio)))
        return rms
    
    def rms_to_db(self, rms: Number):
        return 20 * np.log10(rms / 32768.0)

    def get_db(self, audio_bytes: bytes):
        rms = self.get_rms(audio_bytes)
        return self.rms_to_db(rms)
    
    def write_audio(
        self, audio_bytes: bytes, channels: int, sample_rate: int, sample_width: int
    ) -> str:
        """Writes audio to an output file"""
        output_file = self.output_file
        with wave.open(output_file, "wb") as wf:
            wf.setnchannels(channels)
            wf.setframerate(sample_rate)
            wf.setsampwidth(sample_width)
            wf.writeframes(audio_bytes)
        return output_file

    def record_and_write(self, duration) -> str:
        """Records from microphone while the button is held down,
        returns a resulting output audio file"""
        # self.led.on()
    
        self.audio_playback(self.wake_signal)

        channels, sample_rate = (
            self.channels,
            self.sample_rate,
        )
        format, p, chunk = self.format, self.p, self.chunk
        stream = p.open(
            format=self.format,
            channels=self.channels,
            rate=sample_rate,
            frames_per_buffer=self.chunk,
            input=True,
        )

        audio_bytes, count = bytearray(), 0
        while count < duration:
            for _ in range(0, int(sample_rate / chunk)):
                data = stream.read(chunk)
                audio_bytes.extend(data)
            count += 1
        stream.stop_stream()
        stream.close()
        p.terminate()
        self.write_audio(
            audio_bytes=audio_bytes,
            channels=channels,
            sample_rate=sample_rate,
            sample_width=p.get_sample_size(format),
        )
        # self.led.off()
        dbfs = self.get_db(audio_bytes=audio_bytes)
        dbfs < self.dBFS_silence_threshold and print("SILENCE DETECTED")
    def audio_playback(self, audio_file):
        subprocess.Popen(["mpg123", audio_file]).wait()

In [495]:
at = AudioTools()

at.record_and_write(duration=3)

High Performance MPEG 1.0/2.0/2.5 Audio Player for Layers 1, 2 and 3
	version 1.32.4; written and copyright by Michael Hipp and others
	free software (LGPL) without any warranty but with best wishes

Playing MPEG stream 1 of 1: dearearth.mp3 ...

MPEG 1.0 L III vbr 44100 j-s

	Title:   
	Artist:  
	Album:   
	Year:    
	Genre:   
	Comment: 



[0:01] Decoding of dearearth.mp3 finished.


In [462]:
with open("input_query.wav", "rb") as f:
    print(at.get_db(f.read()))

0.0018926322809420526


In [ ]:
wi

In [ ]:
from pydub import AudioSegment




In [232]:
c = scipy.io.wavfile.read("input_query.wav")

In [233]:
np20 * np.log10(np.abs(np.fft.rfft(c[1])))

array([97.30468605, 96.84078428, 96.31527676, ..., 50.34913724,
       49.38717596, 50.68052212])

In [240]:
m = np.max(np.frombuffer(i.getvalue(), dtype=np.int16))

In [241]:
20 * np.log(m)

204.80348587036133

In [273]:
pydub.AudioSegment.from_raw(i.getvalue(), 2)

TypeError: AudioSegment.from_raw() takes 2 positional arguments but 3 were given

In [274]:
# for b in audio:
#     rms += np.square(b / 32768.0)

array([ 18770,  17990,     36,      0,  16727,  17750,  28006,   8308,
           16,      0,      1,      1, -21436,      0,  22664,      1,
            2,     16,  24932,  24948,      0,      0], dtype=int16)

In [288]:
20 * np.log10(np.sqrt(np.mean(np.square(audio))))

36.547539332529304

In [308]:
a = np.frombuffer(audio, dtype=np.int16).astype(np.float32)
np.sqrt(np.mean(np.square(a)))

In [314]:
np.sqrt(np.mean(np.square(a)))

14047.541

14250

In [367]:
import whisper


model = whisper.load_model("tiny")

a = whisper.load_audio("input_query.wav")
whisper.transcribe(model=model, audio=a, initial_prompt="If there is no speech, do not transcribe any text")

/Users/lucacaputo/miniconda3/envs/notebook/lib/python3.11/site-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


{'text': ' If there is no speech, do not transcribe any text.',
 'segments': [{'id': 0,
   'seek': 0,
   'start': 0.0,
   'end': 10.0,
   'text': ' If there is no speech, do not transcribe any text.',
   'tokens': [50364,
    759,
    456,
    307,
    572,
    6218,
    11,
    360,
    406,
    1145,
    8056,
    604,
    2487,
    13,
    50864],
   'temperature': 0.0,
   'avg_logprob': -0.6199649572372437,
   'compression_ratio': 0.8928571428571429,
   'no_speech_prob': 0.41126808524131775}],
 'language': 'nn'}

In [362]:
with open("input_query.wav", "rb") as f:
    audio = f.read()

In [363]:
 a = np.frombuffer(audio, np.int16) / 32768
 20 * np.log10(np.abs(a), where=a>0)

array([ -4.83971325,  -5.20837543,  -1.14893995, ..., -55.82348131,
       -55.6611235 , -55.19150159])

In [366]:
a[a > 0.5]

array([0.57281494, 0.54901123, 0.87609863, 0.51046753, 0.54168701,
       0.85467529, 0.69165039, 0.76086426, 0.76135254, 0.875     ])

In [373]:
def detect(audio, threshold):
    trim_ms = 0
    chunk_size = 128
    while (audio[trim_ms:trim_ms + chunk_size].dBFS < threshold 
           and trim_ms < len(audio)):
        trim_ms += chunk_size
    return trim_ms, len(audio)

In [374]:
from pydub import AudioSegment

a = AudioSegment.from_file("input_query.wav", format="wav")

In [379]:
with open("input_query.wav", "rb") as f:
    a1 = f.read()

In [440]:
with open("../input_query.wav", "rb") as f:
    a2 = f.read()

In [441]:

def get_rms(audio_bytes):
    return np.sqrt(np.mean(np.square(
            np.frombuffer(
                audio_bytes,
                dtype=np.int16)
            .astype(np.float32)
        )))

In [472]:
aa = np.frombuffer(a4, dtype=np.int16).astype(np.float32)
np.sqrt(np.mean(np.square(aa))) / 32768, get_rms(a4) / 32768

(0.05045197159051895, 0.05045197159051895)

In [471]:
np.sqrt(np.mean(np.square(np.frombuffer(a4, dtype=np.int16).astype(np.float32))))

1653.2102

In [442]:
20 * np.log10(get_rms(a1) / 32768)

-47.52201576317589

In [437]:
20 * np.log10(get_rms(a2) / 32768)

-39.4533454211059

In [426]:
with open("input_query.wav", "rb") as f:
    a3 = f.read()

In [427]:
20 * np.log10(get_rms(a3) / 32768.0)

-26.72835248870035

In [428]:
AudioSegment.from_file("input_query.wav", format="wav").dBFS

-26.775600045831368

In [429]:
%%timeit -n 1000
20 * np.log10(get_rms(a2) / 32768)

34.5 µs ± 3.56 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [435]:
%%timeit -n 1000
AudioSegment(a2).dBFS

122 µs ± 3.76 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [439]:
AudioSegment.from_file("../input_query.wav", format="wav").dBFS

-68.72537377824186

In [456]:
with open("input_query.wav", "rb") as f:
    a4 = f.read()

In [458]:
print(20 * np.log10(get_rms(a4) / 32768))

-25.942437149828944


In [459]:
get_rms(a4)

1653.2102

In [463]:
aa = np.frombuffer(a4, dtype=np.int16).astype(np.float32)

In [468]:
np.sqrt(np.mean(np.square(aa))) / 32768, get_rms(aa) / 32768

(0.05045197159051895, 0.5188338756561279)

In [480]:
with open("input_query.wav", "rb") as f:
    a4 = f.read()
    
print(get_rms(a4))

1323.3127


In [483]:
20 * np.log(get_rms(a4) / 32768)

-64.18628364182

In [498]:
import io

In [506]:
%%timeit -n 100

i = io.BytesIO()
for _ in range(10):
    i.write(b"ndfasndfnasf" * 1000)
i.getvalue()

9.38 µs ± 2.3 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [553]:
from io import BytesIO
from numbers import Number
import numpy as np


class AudioRecording(BytesIO):
    def __init__(self, name: str, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.name = name

    def get_rms(self, buffer: bytes):
        audio = np.frombuffer(buffer, dtype=np.int16).astype(np.float32)
        rms = np.sqrt(np.mean(np.square(audio)))
        return rms
    
    def rms_to_db(self, rms: Number):
        return 20 * np.log10(rms / 32768.0)

    def get_decibles(self, audio_bytes: bytes):
        rms = self.get_rms(audio_bytes)
        return self.rms_to_db(rms)
    
    @property
    def volume(self):
        return self.get_decibles(self.getvalue())
    
    

In [675]:

class AudioTools:
    __slots__ = (
        "channels",
        "sample_rate",
        "chunk",
        "format",
        "output_file",
        "button",
        "_buffer",
        "wake_signal",
        "tts_format",
        "silence_threshold"
    )

    def __init__(self):
        params = self.p.get_default_input_device_info()
        self.channels = int(params["maxInputChannels"])
        self.sample_rate = int(params["defaultSampleRate"])
        self.chunk = 128  # TODO: FIGURE OUT A GOOD NUMBER?
        self.format = pyaudio.paInt16
        # button.when_pressed = self.record
        # self.button = button
        config = Config()
        output_file = config.audio_output_file
        self.output_file = output_file #write the recordings to model's entrypoint
        self.wake_signal = config.wake_signal_audio
        self.tts_format = config.tts_file_format
        # self.led = led
        self.silence_threshold = -30.0
        self._buffer = AudioRecording(name=output_file)

    @property
    def p(self):
        return pyaudio.PyAudio()
    
    @property 
    def audio_bytes(self):
        audio_bytes = self._buffer
        if not audio_bytes: 
            self.new_recording()
            return audio_bytes
        if audio_bytes.volume < self.silence_threshold:
            return None
        self.new_recording()
        audio_bytes.seek(0)
        return audio_bytes
        
    def new_recording(self):
        print("new recording")
        self._buffer = AudioRecording(name=self.output_file)

    def write_audio(self, audio: bytes, channels: int, sample_rate: int, sample_width: int) -> str:
        """Writes audio to an output file"""
        with wave.open(self._buffer, "wb") as wf:
            wf.setnchannels(channels)
            wf.setframerate(sample_rate)
            wf.setsampwidth(sample_width)
            wf.writeframes(audio)

    def record(self, duration) -> str: #pragma: no cover; see tests/device/test_audio.py
        """Records from microphone while the button is held down,
        returns a resulting output audio file"""
        self.audio_playback(self.wake_signal)
        
        channels, sample_rate = self.channels, self.sample_rate
        format, p, chunk = self.format, self.p, self.chunk
        stream = p.open(
            format=self.format,
            channels=self.channels,
            rate=sample_rate,
            frames_per_buffer=self.chunk,
            input=True,
        )

        audio_buffer, count = self._buffer, 0
        while (count < duration):
            for _ in range(0, int(sample_rate / chunk)):
                audio_buffer.write(stream.read(chunk))
            count += 1
        stream.stop_stream()
        stream.close()
        p.terminate()
        audio_bytes = self.audio_bytes
        if audio_bytes:            
            self.write_audio(
                audio=audio_bytes.getvalue(),
                channels=channels,
                sample_rate=sample_rate,
                sample_width=p.get_sample_size(format),
            )
        # led.off()
        else: self._buffer = None
        
    def audio_playback(self, audio_file: str) -> None:
        subprocess.Popen(["mpg123", "-q", audio_file]).wait()

In [676]:
at = AudioTools()

at.record(duration=5)

new recording


In [683]:
import wave

audio_bytes = at.audio_bytes
print(audio_bytes)
if audio_bytes:
    with wave.open("input_quer.wav", "wb") as wf:
        wf.setnchannels(1)
        wf.setframerate(44100)
        wf.setsampwidth(2)
        wf.writeframes(audio_bytes.getvalue())
else: print("skipping")

new recording
None
skipping


In [682]:
at.record(duration=5)

In [515]:
def hey(vol):
    if vol < 1:
        return
    print("hey")

In [516]:
hey(vol=0)

In [691]:
from_cpi = pd.read_csv("../data/average-cpis.csv").iloc[:, -6:]

In [690]:
codes = pd.read_csv("../../Downloads/iso-country-codes (1).csv")

In [694]:
merged = from_cpi.merge(codes, on=[col for col in from_cpi if col in codes])

In [695]:
merged

iso_currency_code    currency      French short name region_code  \
0                afn     Afghani       Afghanistan (l')          AF   
1                dzd       Dinar           Algérie (l')          DZ   
2                ars        Peso         Argentine (l')          AR   
3                aud      Dollar         Australie (l')          AU   
4                bhd       Dinar                Bahreïn          BH   
5                brl        Real            Brésil (le)          BR   
6                cad      Dollar            Canada (le)          CA   
7                cny        Yuan             Chine (la)          CN   
8                dkk       Krone          Danemark (le)          DK   
9                egp       Pound            Égypte (l')          EG   
10               hkd      Dollar              Hong Kong          HK   
11               huf      Forint           Hongrie (la)          HU   
12               isk       Krona           Islande (l')          IS   
13               inr       Rupee              Inde (l')          IN   
14               iqd       Dinar              Iraq (l')          IQ   
15               ils  New Shekel                 Israël          IL   
16               jpy         Yen             Japon (le)          JP   
17               lbp       Pound             Liban (le)          LB   
18               mxn        Peso           Mexique (le)          MX   
19               mad      Dirham             Maroc (le)          MA   
20               nzd      Dollar  Nouvelle-Zélande (la)          NZ   
21               nok      Kroner           Norvège (la)          NO   
22               qar        Rial             Qatar (le)          QA   
23               rub       Ruble                    NaN          RU   
24               sar       Riyal   Arabie saoudite (l')          SA   
25               sgd      Dollar              Singapour          SG   
26               zar        Rand    Afrique du Sud (l')          ZA   
27               sek       Krona             Suède (la)          SE   
28               chf       Franc            Suisse (la)          CH   
29               twd      Dollar                    NaN          TW   
30               thb        Baht         Thaïlande (la)          TH   
31               tnd       Dinar           Tunisie (la)          TN   
32               try    New Lira                    NaN          TR   
33               aed      Dirham                    NaN          AE   
34               gbp       Pound                    NaN          GB   
35               usd      Dollar                    NaN          US   

   Alpha-3 code  Numeric               country  
0           AFG      4.0           Afghanistan  
1           DZA     12.0               Algeria  
2           ARG     32.0             Argentina  
3           AUS     36.0             Australia  
4           BHR     48.0               Bahrain  
5           BRA     76.0                Brazil  
6           CAN    124.0                Canada  
7           CHN    156.0                 China  
8           DNK    208.0               Denmark  
9           EGY    818.0                 Egypt  
10          HKG    344.0             Hong Kong  
11          HUN    348.0               Hungary  
12          ISL    352.0               Iceland  
13          IND    356.0                 India  
14          IRQ    368.0                  Iraq  
15          ISR    376.0                Israel  
16          JPN    392.0                 Japan  
17          LBN    422.0               Lebanon  
18          MEX    484.0                Mexico  
19          MAR    504.0               Morocco  
20          NZL    554.0           New Zealand  
21          NOR    578.0                Norway  
22          QAT    634.0                 Qatar  
23          NaN      NaN                Russia  
24          SAU    682.0          Saudi Arabia  
25          SGP    702.0             Singapore  
26          ZAF    710.0          South Africa  
27 

In [696]:
merged.to_csv("../data/country-codes.csv", index=None)